In [9]:
import sys
print("当前内核 Python 路径：", sys.executable)
import sys
!{sys.executable} -m pip install matplotlib

当前内核 Python 路径： /home/sunjingyi/.conda/envs/sjy_python/bin/python
  Using cached cycler-0.12.1-py3-none-any.whl.metadata (3.8 kB)
  Using cached pyparsing-3.2.3-py3-none-any.whl.metadata (5.0 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.7/8.7 MB 74.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.0/5.0 MB 70.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 6.7 MB/s eta 0:00:00-:--:--
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.6/6.6 MB 61.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7/7 [matplotlib]7 [matplotlib]


In [ ]:

import numpy as np
import matplotlib.pyplot as plt
from matplotlib import animation
from IPython.display import HTML  # 在 Jupyter 里内联显示动画

# =============== 1) 生成模拟数据（1D 特征，便于画直线） ===============
np.random.seed(0)
n = 80
X = np.linspace(-3, 3, n).reshape(-1, 1)         # (n, 1)
true_w, true_b = 1.5, -0.8
noise = 0.6 * np.random.randn(n)
y = true_w * X[:, 0] + true_b + noise            # 目标 (n,)

# =============== 2) 定义训练超参数与容器 ===============
lr = 0.05
epochs = 120  # 动画帧数
w, b = 0.0, 0.0

# 记录每一步（用于动画）
hist_w, hist_b, hist_loss = [], [], []

# =============== 3) 梯度下降训练（记录每轮） ===============
for t in range(epochs):
    y_hat = w * X[:, 0] + b
    err = y_hat - y
    J = np.mean(err**2)                     # MSE

    # 梯度（未用半 MSE，因此系数 2）
    grad_w = (2 / n) * np.sum(err * X[:, 0])
    grad_b = (2 / n) * np.sum(err)

    # 参数更新
    w -= lr * grad_w
    b -= lr * grad_b

    # 保存历史
    hist_w.append(w)
    hist_b.append(b)
    hist_loss.append(J)

# =============== 4) 设置画布与初始元素 ===============
fig, axes = plt.subplots(1, 2, figsize=(10, 4))
ax_data, ax_loss = axes

# 左图：数据与拟合直线
ax_data.scatter(X[:, 0], y, s=25, c="#4C78A8", alpha=0.8, label="data")
x_line = np.linspace(X.min(), X.max(), 100)
line_fit, = ax_data.plot(x_line, hist_w[0]*x_line + hist_b[0],
                         color="#F58518", lw=2, label="fit")
ax_data.set_title("Gradient Descent on Linear Regression")
ax_data.set_xlabel("x")
ax_data.set_ylabel("y")
ax_data.legend(loc="upper left")
ax_data.grid(alpha=0.3)

# 右图：损失曲线（逐点增加）
ax_loss.set_title("MSE over Iterations")
ax_loss.set_xlabel("iteration")
ax_loss.set_ylabel("MSE")
ax_loss.grid(alpha=0.3)
loss_line, = ax_loss.plot([], [], color="#54A24B", lw=2)
ax_loss.set_xlim(0, epochs)
ax_loss.set_ylim(0, max(hist_loss)*1.05)

# 动态文本：显示当前 w, b, loss
text_box = ax_data.text(0.05, 0.95, "", transform=ax_data.transAxes,
                        va="top", ha="left", fontsize=10,
                        bbox=dict(boxstyle="round", fc="white", ec="gray", alpha=0.8))

# =============== 5) 定义动画更新函数 ===============
def init():
    # 初始化空状态（可选）
    line_fit.set_data(x_line, hist_w[0]*x_line + hist_b[0])
    loss_line.set_data([], [])
    text_box.set_text("")
    return line_fit, loss_line, text_box

def update(frame):
    # 更新左图的拟合直线
    w_t, b_t = hist_w[frame], hist_b[frame]
    y_line = w_t * x_line + b_t
    line_fit.set_data(x_line, y_line)

    # 更新右图的损失曲线
    loss_line.set_data(np.arange(frame+1), hist_loss[:frame+1])

    # 更新文字
    text_box.set_text(f"iter: {frame}\nw: {w_t:.3f}\nb: {b_t:.3f}\nMSE: {hist_loss[frame]:.3f}")
    return line_fit, loss_line, text_box

# =============== 6) 创建并显示动画 ===============
ani = animation.FuncAnimation(
    fig, update, frames=epochs, init_func=init, interval=60, blit=True
)

plt.tight_layout()
plt.close(fig)  # 避免重复静态图

# 在 Jupyter 里内联显示（HTML5 video）
HTML(ani.to_jshtml())

# 如需保存为 GIF，取消下方注释（需要 pillow）
# ani.save("linear_regression_gd.gif", writer="pillow", fps=20)